In [20]:
import numpy as np
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
import pandas as pd
from itertools import product

In [21]:
# Load cleaned and prepared data
data = pd.read_csv('./Data/historical_weather_cleaned_filtered.csv')
data['date'] = pd.to_datetime(data['date'])
data.set_index('date', inplace=True)

In [39]:
avg_temp_df = data.pivot(columns='city_id', values='avg_temp_c')
min_temp_df = data.pivot(columns='city_id', values='min_temp_c')
max_temp_df = data.pivot(columns='city_id', values='max_temp_c')


In [23]:
# Check for nan
print(avg_temp_df.isnull().sum())

city_id
C001     0
C002    23
C003     3
C004     0
C005     0
        ..
C108     0
C109     0
C110     1
C111     7
C112    26
Length: 100, dtype: int64


In [24]:
# Define train and test data periods for each scenario
scenarios = [
    ('2014-01-01', '2017-12-31', '2018-01-01', '2018-01-07'),
    ('2015-01-01', '2017-12-31', '2018-01-01', '2018-01-07'),
    ('2016-01-01', '2017-12-31', '2018-01-01', '2018-01-07'),
    ('2017-01-01', '2017-12-31', '2018-01-01', '2018-01-07')
]

In [25]:
# List to store RMSE values for each scenario
rmse_scenarios = []

# Train a SARIMA model for each city and make predictions for each scenario
for train_start, train_end, test_start, test_end in scenarios:
    train_data = avg_temp_df[train_start:train_end]
    test_data = avg_temp_df[test_start:test_end]

    # Create a DataFrame to store predictions
    predictions = pd.DataFrame(index=test_data.index, columns=avg_temp_df.columns)
    rmse_list = []

    # Train a SARIMA model for each city and make predictions
    for city in avg_temp_df.columns:
        # Train the SARIMA model (seasonal_order can be adjusted based on seasonal patterns)
        model = SARIMAX(train_data[city], order=(5, 1, 0), seasonal_order=(1, 0, 1, 7))  
        model_fit = model.fit(disp=False)
        
        # Forecast the average temperature for the test period
        forecast = model_fit.get_forecast(steps=len(test_data))
        forecast_mean = forecast.predicted_mean
        
        # Store the forecast in the predictions DataFrame
        predictions[city] = forecast_mean.values
        
        # Calculate RMSE for the city
        rmse = np.sqrt(mean_squared_error(test_data[city], forecast_mean))
        rmse_list.append(rmse)

    # Calculate the average RMSE across all cities for the current scenario
    average_rmse = np.mean(rmse_list)
    rmse_scenarios.append(average_rmse)

    # Print or store results as needed
    print(f"Scenario: Train {train_start} to {train_end}, Test {test_start} to {test_end}")
    print("Predictions:")
    print(predictions)
    print(f"Average RMSE across all cities: {average_rmse}")
    print("\n")

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: FutureWarning: No supported index is available. In the 

Scenario: Train 2014-01-01 to 2017-12-31, Test 2018-01-01 to 2018-01-07
Predictions:
city_id         C001       C002       C003      C004       C005       C007  \
date                                                                         
2018-01-01  7.547426  14.729365  25.242778 -2.527643  26.233620  19.190517   
2018-01-02  7.813564  15.575098  25.270770 -1.385569  26.306399  18.002998   
2018-01-03  8.373856  15.699989  25.092794 -1.429850  26.641749  17.894267   
2018-01-04  8.201169  15.592071  25.279346 -1.606756  26.855820  18.175663   
2018-01-05  8.317313  15.574435  25.236505 -1.811588  26.779995  18.583870   
2018-01-06  8.334658  15.524746  25.247322 -2.039392  26.653687  18.693109   
2018-01-07  8.648011  15.541715  25.296348 -1.714935  26.731120  18.537957   

city_id          C008       C009       C010      C011  ...      C103  \
date                                                   ...             
2018-01-01  12.442350  19.106008  19.105994  0.233378  ...  1.667141

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been prov

Scenario: Train 2015-01-01 to 2017-12-31, Test 2018-01-01 to 2018-01-07
Predictions:
city_id         C001       C002       C003      C004       C005       C007  \
date                                                                         
2018-01-01  7.507720  14.742600  25.184950 -2.542869  26.313146  19.117368   
2018-01-02  7.773768  15.607535  25.300118 -1.435868  26.415285  18.036040   
2018-01-03  8.270435  15.821861  25.079652 -1.404431  26.736043  18.075528   
2018-01-04  8.133009  15.776369  25.249342 -1.529359  26.910333  18.354314   
2018-01-05  8.342302  15.721717  25.259514 -1.818174  26.812250  18.678271   
2018-01-06  8.318988  15.586471  25.240960 -2.031478  26.690112  18.692851   
2018-01-07  8.601645  15.561097  25.294413 -1.741611  26.848853  18.512573   

city_id          C008       C009       C010      C011  ...      C103  \
date                                                   ...             
2018-01-01  12.045572  19.088172  19.093701  0.314705  ...  1.493903

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been prov

Scenario: Train 2016-01-01 to 2017-12-31, Test 2018-01-01 to 2018-01-07
Predictions:
city_id         C001       C002       C003      C004       C005       C007  \
date                                                                         
2018-01-01  7.644062  14.757712  25.164720 -2.583586  26.385514  19.258039   
2018-01-02  7.849844  15.550432  25.308650 -1.426329  26.571154  18.027704   
2018-01-03  8.345980  15.682338  25.111559 -1.444549  26.876754  17.798830   
2018-01-04  8.293287  15.643972  25.376255 -1.596663  27.067353  17.925312   
2018-01-05  8.440493  15.665284  25.294958 -1.823382  27.047518  18.395829   
2018-01-06  8.371200  15.541164  25.328309 -1.992205  26.923259  18.618391   
2018-01-07  8.613633  15.510802  25.389672 -1.762732  27.116576  18.514059   

city_id          C008       C009       C010      C011  ...      C103  \
date                                                   ...             
2018-01-01  12.128737  19.098763  19.090149  0.524680  ...  1.461249

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\s

Scenario: Train 2017-01-01 to 2017-12-31, Test 2018-01-01 to 2018-01-07
Predictions:
city_id         C001       C002       C003      C004       C005       C007  \
date                                                                         
2018-01-01  7.620844  14.687506  25.055507 -2.681826  26.488834  19.320589   
2018-01-02  7.649963  15.540047  25.207319 -1.713412  26.864902  18.063685   
2018-01-03  8.117774  15.678771  25.147358 -1.816407  27.101772  17.795892   
2018-01-04  8.110332  15.636645  25.420435 -1.916456  27.265303  17.886682   
2018-01-05  8.307961  15.616418  25.336990 -2.232187  27.372543  18.470456   
2018-01-06  8.294576  15.622016  25.358095 -2.188452  27.182189  18.663923   
2018-01-07  8.619775  15.653135  25.456620 -1.818459  27.391544  18.587890   

city_id          C008       C009       C010      C011  ...      C103  \
date                                                   ...             
2018-01-01  12.457225  19.179609  19.039341  1.159074  ...  1.451795

In [26]:
# Print RMSE values for all scenarios
for i, rmse in enumerate(rmse_scenarios):
    print(f"Scenario {i+1} RMSE: {rmse}")

Scenario 1 RMSE: 2.366023532444127
Scenario 2 RMSE: 2.376607041959623
Scenario 3 RMSE: 2.3823096529935937
Scenario 4 RMSE: 2.386514697143216


In [28]:
# List to store RMSE values for each scenario
rmse_scenarios = []

# Train and test SARIMA models for each scenario
for train_start, train_end, test_start, test_end in scenarios:
    train_data = avg_temp_df[train_start:train_end]
    test_data = avg_temp_df[test_start:test_end]

    # Create a DataFrame to store predictions
    predictions = pd.DataFrame(index=test_data.index, columns=avg_temp_df.columns)

    # Train a SARIMA model for each city and make predictions
    for city in avg_temp_df.columns:
        # Train the SARIMA model (seasonal_order can be adjusted based on seasonal patterns)
        model = SARIMAX(train_data[city], order=(5, 1, 0), seasonal_order=(1, 0, 1, 7))  
        model_fit = model.fit(disp=False)
        
        # Forecast the average temperature for the test period
        forecast = model_fit.get_forecast(steps=len(test_data))
        forecast_mean = forecast.predicted_mean
        
        # Store the forecast in the predictions DataFrame
        predictions[city] = forecast_mean.values
    
    # Calculate average predicted temperatures across all cities for the current scenario
    average_predicted_temps = predictions.mean(axis=1)
    
    # Calculate RMSE for the scenario using average predicted temperatures and actual temperatures
    rmse = np.sqrt(mean_squared_error(test_data.mean(axis=1), average_predicted_temps))
    rmse_scenarios.append(rmse)

# Calculate the average RMSE across all scenarios
average_rmse_all_scenarios = np.mean(rmse_scenarios)

# Print or store results as needed
print("Average RMSE across all scenarios:")
print(average_rmse_all_scenarios)

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: FutureWarning: No supported index is available. In the 

Average RMSE across all scenarios:
0.6838132129648085


In [36]:
# List to store RMSE values for each scenario
rmse_scenarios = []

# Train and test SARIMA models for each scenario
for train_start, train_end, test_start, test_end in scenarios:
    train_data = avg_temp_df[train_start:train_end]
    test_data = avg_temp_df[test_start:test_end]

    # Create a DataFrame to store predictions
    predictions = pd.DataFrame(index=test_data.index, columns=avg_temp_df.columns)

    # Train a SARIMA model for each city and make predictions
    for city in avg_temp_df.columns:
        # Train the SARIMA model (seasonal_order can be adjusted based on seasonal patterns)
        model = SARIMAX(train_data[city], order=(5, 1, 0), seasonal_order=(1, 0, 1, 7))  
        model_fit = model.fit(disp=False)
        
        # Forecast the average temperature for the test period (January 1, 2019, to January 7, 2019)
        forecast = model_fit.get_forecast(steps=7)
        forecast_mean = forecast.predicted_mean
        
        # Store the forecast in the predictions DataFrame
        predictions[city] = forecast_mean.values
    
    # Update submission_key.csv with predicted temperatures
    submission_key = pd.read_csv('./Data/submission_key.csv')
    
    for idx, row in submission_key.iterrows():
        city_id = row['city_id']
        date = row['date']
        avg_temp = predictions[city_id][(pd.to_datetime(date) - pd.to_datetime('2019-01-01')).days]
        submission_key.loc[idx, 'avg_temp_c'] = avg_temp
    
    # Create submission DataFrame with submission_ID and avg_temp_c
    submission = submission_key[['submission_ID', 'avg_temp_c']]
    
    # Save the submission to CSV
    submission.to_csv('./Data/submission_avg.csv', index=False)

print("Predicted temperatures for submission saved to submission_avg.csv.")

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: FutureWarning: No supported index is available. In the 

Predicted temperatures for submission saved to submission_avg.csv.


C:\Users\kauad\AppData\Local\Temp\ipykernel_9376\1010337015.py:31: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  avg_temp = predictions[city_id][(pd.to_datetime(date) - pd.to_datetime('2019-01-01')).days]
C:\Users\kauad\AppData\Local\Temp\ipykernel_9376\1010337015.py:31: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  avg_temp = predictions[city_id][(pd.to_datetime(date) - pd.to_datetime('2019-01-01')).days]
C:\Users\kauad\AppData\Local\Temp\ipykernel_9376\1010337015.py:31: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (con

In [37]:
# Function to predict and update submission_key.csv
def predict_and_update_submission(scenarios):
    # List to store RMSE values for each scenario
    rmse_scenarios = []

    # Iterate over each scenario
    for train_start, train_end, test_start, test_end in scenarios:
        train_data = avg_temp_df[train_start:train_end]
        test_data = avg_temp_df[test_start:test_end]

        # Create a DataFrame to store predictions
        predictions = pd.DataFrame(index=test_data.index, columns=avg_temp_df.columns)

        # Train a SARIMA model for each city and make predictions
        for city in avg_temp_df.columns:
            # Train the SARIMA model (seasonal_order can be adjusted based on seasonal patterns)
            model = SARIMAX(train_data[city], order=(5, 1, 0), seasonal_order=(1, 0, 1, 7))  
            model_fit = model.fit(disp=False)
            
            # Forecast the average temperature for the test period (January 1, 2019, to January 7, 2019)
            forecast = model_fit.get_forecast(steps=7)
            forecast_mean = forecast.predicted_mean
            
            # Store the forecast in the predictions DataFrame
            predictions[city] = forecast_mean.values
        
        # Update submission_key.csv with predicted temperatures
        submission_key = pd.read_csv('./Data/submission_key.csv')
        
        for idx, row in submission_key.iterrows():
            city_id = row['city_id']
            date = row['date']
            avg_temp = predictions[city_id][(pd.to_datetime(date) - pd.to_datetime('2019-01-01')).days]
            submission_key.loc[idx, 'avg_temp_c'] = avg_temp
        
        # Calculate RMSE for the scenario (optional)
        rmse = np.sqrt(np.mean((test_data.mean(axis=1) - predictions.mean(axis=1)) ** 2))
        rmse_scenarios.append(rmse)
        
        # Save updated submission_key.csv back to file
        submission_key.to_csv('./Data/submission_avg2.csv', index=False)
    
    # Calculate and print average RMSE across all scenarios
    average_rmse_all_scenarios = np.mean(rmse_scenarios)
    print(f"Average RMSE across all scenarios: {average_rmse_all_scenarios}")

# Call the function to predict and update submission_key.csv
predict_and_update_submission(scenarios)

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: FutureWarning: No supported index is available. In the 

Average RMSE across all scenarios: 0.6838132129648085


C:\Users\kauad\AppData\Local\Temp\ipykernel_9376\2371108644.py:33: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  avg_temp = predictions[city_id][(pd.to_datetime(date) - pd.to_datetime('2019-01-01')).days]
C:\Users\kauad\AppData\Local\Temp\ipykernel_9376\2371108644.py:33: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  avg_temp = predictions[city_id][(pd.to_datetime(date) - pd.to_datetime('2019-01-01')).days]
C:\Users\kauad\AppData\Local\Temp\ipykernel_9376\2371108644.py:33: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (con

In [38]:
# List to store RMSE values for each scenario
rmse_scenarios = []

# Initialize a DataFrame to aggregate predictions
predictions_ensemble = pd.DataFrame(index=avg_temp_df.index, columns=avg_temp_df.columns)

# Train and predict using SARIMA models for each scenario
for train_start, train_end, test_start, test_end in scenarios:
    train_data = avg_temp_df[train_start:train_end]
    test_data = avg_temp_df[test_start:test_end]

    # DataFrame to store predictions for the current scenario
    predictions = pd.DataFrame(index=test_data.index, columns=avg_temp_df.columns)

    # Train a SARIMA model for each city and make predictions
    for city in avg_temp_df.columns:
        # Train the SARIMA model (seasonal_order can be adjusted based on seasonal patterns)
        model = SARIMAX(train_data[city], order=(5, 1, 0), seasonal_order=(1, 0, 1, 7))  
        model_fit = model.fit(disp=False)
        
        # Forecast the average temperature for the test period
        forecast = model_fit.get_forecast(steps=len(test_data))
        forecast_mean = forecast.predicted_mean
        
        # Store the forecast in the predictions DataFrame
        predictions[city] = forecast_mean.values
    
    # Aggregate predictions using simple averaging (ensemble learning)
    predictions_ensemble[test_start:test_end] += predictions
    
    # Calculate RMSE for the scenario using average predicted temperatures and actual temperatures
    rmse = np.sqrt(mean_squared_error(test_data.mean(axis=1), predictions.mean(axis=1)))
    rmse_scenarios.append(rmse)

# Average the ensemble predictions across scenarios
predictions_ensemble /= len(scenarios)

# Calculate the average RMSE across all scenarios
average_rmse_all_scenarios = np.mean(rmse_scenarios)

# Print or store results as needed
print("Average RMSE across all scenarios:")
print(average_rmse_all_scenarios)

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: FutureWarning: No supported index is available. In the 

KeyboardInterrupt: 

In [40]:
# List to store RMSE values for each scenario
rmse_scenarios = []

# Train and test SARIMA models for each scenario
for train_start, train_end, test_start, test_end in scenarios:
    train_min_temp = min_temp_df[train_start:train_end]
    train_max_temp = max_temp_df[train_start:train_end]
    test_min_temp = min_temp_df[test_start:test_end]
    test_max_temp = max_temp_df[test_start:test_end]

    # Create a DataFrame to store predictions
    predictions_min = pd.DataFrame(index=test_min_temp.index, columns=min_temp_df.columns)
    predictions_max = pd.DataFrame(index=test_max_temp.index, columns=max_temp_df.columns)

    # Train a SARIMA model for each city and make predictions for min and max temperatures
    for city in min_temp_df.columns:
        # Train the SARIMA model for min temperature
        model_min = SARIMAX(train_min_temp[city], order=(5, 1, 0), seasonal_order=(1, 0, 1, 7))  
        model_fit_min = model_min.fit(disp=False)
        
        # Forecast the min temperature for the test period
        forecast_min = model_fit_min.get_forecast(steps=len(test_min_temp))
        forecast_mean_min = forecast_min.predicted_mean
        
        # Store the forecast in the min temperature predictions DataFrame
        predictions_min[city] = forecast_mean_min.values
        
        # Train the SARIMA model for max temperature
        model_max = SARIMAX(train_max_temp[city], order=(5, 1, 0), seasonal_order=(1, 0, 1, 7))  
        model_fit_max = model_max.fit(disp=False)
        
        # Forecast the max temperature for the test period
        forecast_max = model_fit_max.get_forecast(steps=len(test_max_temp))
        forecast_mean_max = forecast_max.predicted_mean
        
        # Store the forecast in the max temperature predictions DataFrame
        predictions_max[city] = forecast_mean_max.values
    
    # Calculate average predicted temperatures across all cities for the current scenario
    average_predicted_min_temps = predictions_min.mean(axis=1)
    average_predicted_max_temps = predictions_max.mean(axis=1)
    
    # Combine min and max temperatures into average temperatures
    average_predicted_temps = (average_predicted_min_temps + average_predicted_max_temps) / 2
    
    # Calculate RMSE for the scenario using average predicted temperatures and actual temperatures
    actual_temps = (test_min_temp.mean(axis=1) + test_max_temp.mean(axis=1)) / 2
    rmse = np.sqrt(mean_squared_error(actual_temps, average_predicted_temps))
    rmse_scenarios.append(rmse)

# Calculate the average RMSE across all scenarios
average_rmse_all_scenarios = np.mean(rmse_scenarios)

# Print or store results as needed
print("Average RMSE across all scenarios:")
print(average_rmse_all_scenarios)

c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kauad\AppData\Local\Programs\Python\Python312\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:836: FutureWarning: No supported index is available. In the 

Average RMSE across all scenarios:
0.6788002642219104
